
<div style="text-align: center; line-height: 0; padding-top: 9px;">
  <img src="https://databricks.com/wp-content/uploads/2018/03/db-academy-rgb-1200px.png" alt="Databricks Learning">
</div>


## DEMO - Build and Register a RAG Model

A Retrieval-Augmented Generation (RAG) model is a widely used architecture for generative AI applications, particularly when contextual information needs to accompany the prompt. **In this demo, we will construct a RAG pipeline and register it in the Unity Catalog model registry.**

The RAG pipeline will function as a simple **product design chatbot**. As contextual information, we will provide product descriptions that have previously **listed on Etsy website**. Please note that the dataset **we will use is publicly available, and the large language model (LLM) might already include this data in its training set**. Consequently, the quality of responses with and without contextual data might not differ significantly. In a real-world scenario, the contextual data would include information that is new to the LLM.

**Learning Objectives:**

By the end of this demo, you will be able to:

- Inspect the Vector Search endpoint and index using the UI.

- Set up a Vector Search index using an existing Delta table.

- Retrieve documents from the vector store using similarity search.

- Assemble a RAG pipeline by integrating various components.

- Register a RAG pipeline in the Model Registry.

## REQUIRED - SELECT CLASSIC COMPUTE
Before executing cells in this notebook, please select your classic compute cluster in the lab. Be aware that **Serverless** is enabled by default.

Follow these steps to select the classic compute cluster:
1. Navigate to the top-right of this notebook and click the drop-down menu to select your cluster. By default, the notebook will use **Serverless**.

2. If your cluster is available, select it and continue to the next cell. If the cluster is not shown:

   - Click **More** in the drop-down.
   
   - In the **Attach to an existing compute resource** window, use the first drop-down to select your unique cluster.

**NOTE:** If your cluster has terminated, you might need to restart it in order to select it. To do this:

1. Right-click on **Compute** in the left navigation pane and select *Open in new tab*.

2. Find the triangle icon to the right of your compute cluster name and click it.

3. Wait a few minutes for the cluster to start.

4. Once the cluster is running, complete the steps above to select your cluster.

## Requirements

Please review the following requirements before starting the lesson:

* To run this notebook, you need to use one of the following Databricks runtime(s): **16.2.x-cpu-ml-scala2.12**



## Classroom Setup

Install required libraries.

In [0]:
%pip install -qq -U databricks-sdk langchain-databricks databricks-vectorsearch langchain==0.3.7 langchain-community==0.3.7
dbutils.library.restartPython()

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
%run ../Includes/Classroom-Setup-02


The examples and models presented in this course are intended solely for demonstration and educational purposes.
 Please note that the models and prompt examples may sometimes contain offensive, inaccurate, biased, or harmful content.


'labuser10813094_1751481371'

In [0]:
# assign vs search endpoint by username
vs_endpoint_prefix = "vs_endpoint_"
vs_endpoint_name = vs_endpoint_prefix+str(get_fixed_integer(DA.unique_name("_")))
vs_source_table_name = f"{DA.catalog_name}.{DA.schema_name}.product_text"
vs_index_table_name = f"{DA.catalog_name}.{DA.schema_name}.product_embeddings"

print(f"=== Variables that you will need for this demo === \n")
print(f"Catalog Name                : {DA.catalog_name}\n")
print(f"Schema Name                 : {DA.schema_name}\n")
print(f"Assigned VS endpoint name   : {vs_endpoint_name} \n")
print(f"VS source table name        : {vs_source_table_name} \n")
print(f"VS index table name         : {vs_index_table_name } \n")

=== Variables that you will need for this demo === 

Catalog Name                : dbacademy

Schema Name                 : labuser10813094_1751481371

Assigned VS endpoint name   : vs_endpoint_4 

VS source table name        : dbacademy.labuser10813094_1751481371.product_text 

VS index table name         : dbacademy.labuser10813094_1751481371.product_embeddings 



## Demo Overview

The initial component of this demonstration is the **retrieval component**. Based on the input query, we will search for and retrieve similar product descriptions.

Next, we will construct the entire pipeline using LangChain. **Please note that LangChain is not within the scope of this course. For more information, we recommend referring to the "Generative AI Engineering with Databricks" course.**



## Load Dataset

Before you start building the AI chain, you need to load and prepare the dataset and save it as a Delta table.  
For this demo, we will use the **[Databricks Documentation Dataset](/marketplace/consumer/listings/03bbb5c0-983d-4523-833a-57e994d76b3b?o=1120757972560637)** available from the Databricks Marketplace.

This dataset contains documentation pages with associated `id`, `url`, and `content`.  
We will format the data to create a single unified `document` field combining the URL and content, which will then be used to build a Vector Store.

The table will be created for you in the next code block.

In [0]:
DA.validate_table("dbacademy_docs.v01.docs")

# Read dataset from marketplace
dataset = spark.sql(f"""
        SELECT 
            id AS id, 
            CONCAT('## URL: ', url, '\n\n## Content: ', content) AS document 
        FROM dbacademy_docs.v01.docs
    """)

# Create a delta table for the dataset
vvs_source_table_name = f"{DA.catalog_name}.{DA.schema_name}.docs"
dataset.write.mode("overwrite").option("overwriteSchema", "true").saveAsTable(vs_source_table_name)

# Enable Change Data Feed for Delta table
spark.sql(f"ALTER TABLE {vs_source_table_name} SET TBLPROPERTIES (delta.enableChangeDataFeed = true)")

display(spark.sql(f"SELECT * FROM {vs_source_table_name}"))

Validation of table dbacademy_docs.v01.docs complete. No errors found.


id document 25277 ## URL: https://docs.databricks.com/en/ingestion/bad-records.html

## Content: Handle bad records and files 
Databricks provides a number of options for dealing with files that contain bad records. Examples of bad data include: 
Incomplete or corrupt records: Mainly observed in text based file formats like JSON and CSV. For example, a JSON record that doesn’t have a closing brace or a CSV record that doesn’t have as many columns as the header or first record of the CSV file. 
Mismatched data types: When the value for a column doesn’t have the specified or inferred data type. 
Bad field names: Can happen in all file formats, when the column name specified in the file or record has a different casing than the specified or inferred schema. 
Corrupted files: When a file cannot be read, which might be due to metadata or data corruption in binary file types such as Avro, Parquet, and ORC. On rare occasion, might be caused by long-lasting transient failures in the underlying storage system. 
Missing files: A file that was discovered during query analysis time and no longer exists at processing time. 
Use badRecordsPath
Use badRecordsPath
When you set badRecordsPath, the specified path records exceptions for bad records or files encountered during data loading. 
In addition to corrupt records and files, errors indicating deleted files, network connection exception, IO exception, and so on are ignored and recorded under the badRecordsPath. 
Note 
Using the badRecordsPath option in a file-based data source has a few important limitations: 
It is non-transactional and can lead to inconsistent results. 
Transient errors are treated as failures.

Unable to find input file
Unable to find input file
val df = spark.read .option("badRecordsPath", "/tmp/badRecordsPath") .format("parquet").load("/input/parquetFile") // Delete the input parquet file '/input/parquetFile' dbutils.fs.rm("/input/parquetFile") df.show() 
In the above example, since df.show() is unable to find the input file, Spark creates an exception file in JSON format to record the error. For example, /tmp/badRecordsPath/20170724T101153/bad_files/xyz is the path of the exception file. This file is under the specified badRecordsPath directory, /tmp/badRecordsPath. 20170724T101153 is the creation time of this DataFrameReader. bad_files is the exception type. xyz is a file that contains a JSON record, which has the path of the bad file and the exception/reason message.

Input file contains bad record
Input file contains bad record
// Creates a json file containing both parsable and corrupted records Seq("""{"a": 1, "b": 2}""", """{bad-record""").toDF().write.format("text").save("/tmp/input/jsonFile") val df = spark.read .option("badRecordsPath", "/tmp/badRecordsPath") .schema("a int, b int") .format("json") .load("/tmp/input/jsonFile") df.show() 
In this example, the DataFrame contains only the first parsable record ({"a": 1, "b": 2}). The second bad record ({bad-record) is recorded in the exception file, which is a JSON file located in /tmp/badRecordsPath/20170724T114715/bad_records/xyz. The exception file contains the bad record, the path of the file containing the record, and the exception/reason message. After you locate the exception files, you can use a JSON reader to process them. 25278 ## URL: https://docs.databricks.com/en/ingestion/copy-into/configure-data-access.html

## Content: Configure data access for ingestion 
This article describes how admin users can configure access to data in a bucket in Amazon S3 (S3) so that Databricks users can load data from S3 into a table in Databricks. 
This article describes the following ways to configure secure access to source data: 
(Recommended) Create a Unity Catalog volume. 
Create a Unity Catalog external location with a storage credential. 
Launch a compute resource that uses an AWS instance profile. 
Generate temporary credentials (an AWS access key ID, a secret key, and a session token). 
Before you begin
Befor

## Create and Test Vector Index

In this step, we will compute embeddings for a dataset containing information about products and store them in a Vector Search index using Databricks Vector Search.

**🚨IMPORTANT: Vector Search endpoints must be created before running the rest of the demo. These are already created for you in Databricks Lab environment.**

### Creating a Vector Index via UI


**Steps to Create a Vector Index:**

- Navigate to **Catalog** from the left panel and select your course catalog. 

- Choose your schema. Schema name is printed in the top of the notebook. 

- Select the **`product_text`** table created in the previous step. You can find all resource names at the top of this notebook.

- In the top right corner, click **"Create"** and then **"Vector search index"**.

- Enter **`product_embeddings`** as the index name.

- Choose **`id`** as the primary key.

- Choose `document` field as column(s) to sync.

- For embedding source, select **"compute embeddings"**:
  - Choose **`document` column** as the source column.
  - Select **`databricks-gte-large-en`** as the embedding model. Embedding creation will be **managed** by Databricks which means we don't need to manually compute embeddings.
  - Select the endpoint assigned to you. Refer to the top of this notebook for details on the VS endpoint.  

- Set sync mode to **"Triggered"**.

- Finally, click the **"Create"** button.


### (Alternative) Creating a Vector Index via API 

For simplicity, we created the vector index using the UI. However, this process can also be accomplished programmatically using the `databricks-sdk`. For more detailed instructions, please refer to [documentation page](https://docs.databricks.com/en/generative-ai/create-query-vector-search.html#create-index-using-the-python-sdk).

### Testing the Index: Search for Products Similar to the Query

Before building the RAG pipeline, let's check if the index is ready. We will use `similarity_search` function to search for products that are similar to the query text.

In [0]:
from databricks.vector_search.client import VectorSearchClient

vsc = VectorSearchClient(disable_notice=True)

question = "How to use Auto Loader in Databricks?"

try:
    # get index created in the previous step
    index = vsc.get_index(vs_endpoint_name, vs_index_table_name)

    # search for similar documents
    results = index.similarity_search(
        query_text = question,
        columns=["document"],
        num_results=4
    )

    # show the results
    docs = results.get("result", {}).get("data_array", [])
    pprint(docs)

except Exception as e:
    print(f"Error occurred while loading the index. Did you create an index in the previous step?: {e}")

[['## URL: https://docs.databricks.com/en/ingestion/auto-loader/production.html\n'
  '\n'
  '## Content: Configure Auto Loader for production workloads  \n'
  'Databricks recommends that you follow the streaming best practices for running Auto Loader in '
  'production.  \n'
  'Databricks recommends using Auto Loader in Delta Live Tables for incremental data ingestion. '
  'Delta Live Tables extends functionality in Apache Spark Structured Streaming and allows you to '
  'write just a few lines of declarative Python or SQL to deploy a production-quality data '
  'pipeline with:  \n'
  'Autoscaling compute infrastructure for cost savings  \n'
  'Data quality checks with expectations  \n'
  'Automatic schema evolution handling  \n'
  'Monitoring via metrics in the event log  \n'
  'Monitoring Auto Loader\n'
  'Monitoring Auto Loader\n'
  'Querying files discovered by Auto Loader  \n'
  'Note  \n'
  'The cloud_files_state function is available in Databricks Runtime 11.3 LTS and above.  \n


**💡 Question:** Four similar documents are returned. What should we do if we want to **use only two of these documents** or if we want to **add documents into the context based on their importance or higher similarity**?

## Enable MLflow Tracing

MLflow supports auto-logging for LangChain models. Before we begin constructing the chains, we will enable auto-logging as shown below.

In [0]:
import mlflow
mlflow.langchain.autolog()

## Build a RAG Model

With our contextual information prepared and indexed in Vector Search, we can proceed to build a RAG chain.

With MLflow tracing enabled, you will be able to inspect the LangChain pipeline.

**💡 Question:** Which documents are retrieved from Vector Search and used as "context"?

In [0]:
import mlflow
from operator import itemgetter
from databricks.vector_search.client import VectorSearchClient
from langchain_databricks import ChatDatabricks, DatabricksVectorSearch, DatabricksEmbeddings
from langchain.chains import create_retrieval_chain
from langchain.chains.combine_documents import create_stuff_documents_chain
from langchain.prompts import (
    PromptTemplate,
    ChatPromptTemplate,
)
from langchain_core.runnables import RunnableLambda
from langchain_core.runnables import RunnablePassthrough
from langchain_core.output_parsers import StrOutputParser

# define a retriever function that will be used in the chain
def vector_search_as_retriever(persist_dir=None):
    vectorstore = DatabricksVectorSearch(vs_index_table_name)
    return vectorstore.as_retriever(search_kwargs={"k": 3})

# Return the string contents of the most recent messages: [{...}] from the user to be used as input question
def extract_user_query_string(chat_messages_array):
    return chat_messages_array[-1]["content"]

def format_context(docs):
    chunk_contents = [f"Passage: {d.page_content}\n" for d in docs]
    return "".join(chunk_contents)

# define template for prompt
prompt_template = PromptTemplate.from_template(
    """
    You are a documentation assistant. Use the context below to answer the question clearly and accurately.

    <context>
    {context}
    </context>

    Question: {question}

    Answer:
    """
)

# define foundation model for generating responses
model = ChatDatabricks(endpoint="databricks-meta-llama-3-3-70b-instruct", max_tokens = 500, temperature=0.8)

# RAG chain
chain = (
    {
        "question": itemgetter("messages") | RunnableLambda(extract_user_query_string),
        "context": itemgetter("messages")
        | RunnableLambda(extract_user_query_string)
        | vector_search_as_retriever
        | RunnableLambda(format_context),
    }
    | prompt_template
    | model
    | StrOutputParser()
)

# let's give it a try:
input_example = {"messages": [ {"role": "user", "content": "How do I use Delta Lake time travel?"}]}
answer = chain.invoke(input_example)
print(answer)

/root/.ipykernel/38846/command-559311591441418-30654587:44: LangChainDeprecationWarning: Use databricks_langchain.ChatDatabricks
  model = ChatDatabricks(endpoint="databricks-meta-llama-3-3-70b-instruct", max_tokens = 500, temperature=0.8)
/root/.ipykernel/38846/command-559311591441418-30654587:17: LangChainDeprecationWarning: Use databricks_langchain.DatabricksVectorSearch
  vectorstore = DatabricksVectorSearch(vs_index_table_name)


[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True to VectorSearchClient().
To use Delta Lake time travel, you can query a Delta table by adding a clause after the table name specification. The syntax allows you to specify a timestamp or a version. Here are the ways to use Delta Lake time travel:

1. **Using `TIMESTAMP AS OF` clause**: You can specify a timestamp using the `TIMESTAMP AS OF` clause. For example: `SELECT * FROM people10m TIMESTAMP AS OF '2018-10-18T22:15:12.013Z'`
2. **Using `VERSION AS OF` clause**: You can specify a version using the `VERSION AS OF` clause. For example: `SELECT * FROM delta.`/tmp/delta/people10m` VERSION AS OF 123`
3. **Using `@` syntax**: You can use the `@` syntax to specify the timestamp or version as part of the table name. For example: `SELECT * FROM people10m@20190101000000000` or `SELECT * 

Trace(request_id=tr-2cf053dcc50648c6b35c0fe5d8bb5cf8)

## Save the Model to Model Registry in Unity Catalog

Now that our chain is ready and evaluated, we can register it within our Unity Catalog schema. 

After registering the chain, you can view the chain and models in the **Catalog Explorer**.

In [0]:
import mlflow
import langchain
import langchain_community
import databricks.vector_search
from mlflow.models import infer_signature
from mlflow.models.resources import (
    DatabricksVectorSearchIndex
)

# Set Model Registry URI to Unity Catalog
mlflow.set_registry_uri("databricks-uc")

model_name = f"{DA.catalog_name}.{DA.schema_name}.getstarted_genai_rag_demo"
input_example = {"messages": [ {"role": "user", "content": "How to use Auto Loader in Databricks?"}]}

# Register the assembled RAG model in Model Registry with Unity Catalog
with mlflow.start_run(run_name="genai_gs_demo_02_01") as run:
    signature = infer_signature(input_example, answer)
    model_info = mlflow.langchain.log_model(
        lc_model=chain,
        artifact_path="chain",
        input_example=input_example,
        signature=signature,
        pip_requirements=[
            "langchain==" + langchain.__version__,
            "langchain-community==" + langchain_community.__version__,
            "databricks-vectorsearch==" + databricks.vector_search.__version__,
            "langchain-databricks"
        ],
        resources=[
            DatabricksVectorSearchIndex(index_name=vs_index_table_name)
        ]
    )

mlflow.register_model(model_info.model_uri, model_name)

/local_disk0/.ephemeral_nfs/envs/pythonEnv-052f1aec-a3e8-408a-a42a-56130f59c932/lib/python3.12/site-packages/mlflow/langchain/runnables.py:292: UserWarning: Your model contains a class imported from the LangChain partner package `langchain-databricks`. When loading the model back, MLflow will use the community version of the classes instead of the partner packages, which may lead to unexpected behavior. To ensure that the model is loaded correctly, it is recommended to save the model with the 'model-from-code' method instead: https://mlflow.org/docs/latest/models.html#models-from-code
  warnings.warn(


[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True to VectorSearchClient().


Uploading artifacts:   0%|          | 0/23 [00:00<?, ?it/s]

Successfully registered model 'dbacademy.labuser10813094_1751481371.getstarted_genai_rag_demo'.


## Clean up Classroom

**🚨 Warning:** Please refrain from deleting the catalog and tables created in this demo, as they are required for upcoming demonstrations. To clean up the classroom assets, execute the classroom clean-up script provided in the final demo.

## Summary

In this demo, first, we created a "managed" vector search index using a delta table. After creating the index, we searched for documents similar to the input query. In the second part of the demo, we built and registered the RAG pipeline to Unity Catalog Model Registry. Before registering the model, we enabled mlflow's autolog to trace model run. In the next demos, we will show to evaluate the performance of this model and deploy it into production.


&copy; 2025 Databricks, Inc. All rights reserved. Apache, Apache Spark, Spark, the Spark Logo, Apache Iceberg, Iceberg, and the Apache Iceberg logo are trademarks of the <a href="https://www.apache.org/" target="blank">Apache Software Foundation</a>.<br/>
<br/><a href="https://databricks.com/privacy-policy" target="blank">Privacy Policy</a> | 
<a href="https://databricks.com/terms-of-use" target="blank">Terms of Use</a> | 
<a href="https://help.databricks.com/" target="blank">Support</a>